# Using RoBERTa with Fastai Tutorial 

This notebook follows the tutorial @ https://medium.com/@devkosal/using-roberta-with-fastai-for-nlp-7ed3fed21f6c

In [0]:
# !pip install fastai

In [0]:
# a = ["Hello"]
# while True:
#     a.extend(a)

In [0]:
!pip install pytorch_transformers

     |████████████████████████████████| 184kB 4.6MB/s 
     |████████████████████████████████| 1.0MB 9.6MB/s 
     |████████████████████████████████| 870kB 28.5MB/s 
  Created wheel for sacremoses: filename=sacremoses-0.0.38-cp36-none-any.whl size=884628 sha256=9c6571e01c4cb5764d29c2e789e6a12cf48a5b95d74e9c3c121bac15ce22c5f5
  Stored in directory: /root/.cache/pip/wheels/6d/ec/1a/21b8912e35e02741306f35f66c785f3afe94de754a0eaf1422
Successfully built sacremoses


In [0]:
from fastai.text import *
from fastai.metrics import *
from pytorch_transformers import RobertaTokenizer

In [0]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
from google.colab import files
files.upload()

Saving Train_Articles_Binary_Oversampled.csv to Train_Articles_Binary_Oversampled.csv


{'Train_Articles_Binary_Oversampled.csv': b',sentences,Offset\n0,"Ebola Outbreak Confirmed in Democratic Republic of Congo\n\nOn Tuesday, the government of the Democratic Republic of Congo announced an outbreak of Ebola hemorrhagic fever, a deadly virus that causes severe bleeding and organ failure, among other unpleasant symptoms.","[[171, 231, \'Prop_Span\']]"\n1,The declaration was made after two cases of the diseases were confirmed in the Bikoro province in the northwestern part of the country ten months after the end of an earlier outbreak.,[]\n2,"\xc2\xa9 AP Photo / Abbas Dulleh Ebola-Like Marburg Virus Kills Two People in Uganda\nAccording to the country\'s Health Ministry, five samples were taken from suspected cases in Bikoro.",[]\n3,"Out of the five samples sent to the National Institute of Biological Research in Kinshasa, two tested positive for Ebola.",[]\n4,"However, no deaths have been reported among those with the disease.",[]\n5,"""We will gather more samples, conduct c

In [0]:
import pandas as pd
# SLC_Data = pd.read_csv("SLC_train.csv")
# SLC_Data = pd.read_csv("train_data_SLC_new_final_after_comp.csv")
# SLC_Data = pd.read_csv("OversampledTrain_Binary.csv", encoding='unicode_escape')
SLC_Data = pd.read_csv("Train_Articles_Binary_Oversampled.csv")
# SLC_Data = pd.read_csv("output.txt", delimiter = '\t', names = ['label','sentences'])
# SLC_Data = pd.read_csv("/content/drive/My Drive/output.txt", delimiter = '\t', names = ['label','sentences'])
# SLC_Data = SLC_Data.replace({"label": {1:"prop", 0:"no_prop"}})
# SLC_Data = pd.read_csv("/content/drive/My Drive/Training Data Paraphrase Undersample.csv")
# SLC_Data = pd.read_csv("/content/Training Data Paraphrase Undersample.csv")
# SLC_Data = pd.read_csv("/content/drive/My Drive/Training Data Paraphrase Oversample.csv")
# SLC_Data = pd.read_csv("/content/Training Data Paraphrase Oversample (1).csv")
# SLC_Data = pd.read_csv("/content/drive/My Drive/Training Data Paraphrase Oversample.csv")
# print(len(SLC_Data))
# SLC_Data = SLC_Data.replace({"label": {1:"prop", 0:"no_prop"}})
SLC_Data.head()

Unnamed: 0  ...                     Offset
0           0  ...  [[171, 231, 'Prop_Span']]
1           1  ...                         []
2           2  ...                         []
3           3  ...                         []
4           4  ...                         []

[5 rows x 3 columns]

In [0]:
len(SLC_Data)

24128

In [0]:
# len(SLC_Data['Offset'][1]), SLC_Data['Offset'][1]

In [0]:
# Addinf binprop label
bin_lab_prop = []

for i in range(0,len(SLC_Data),1):
    # sent.append(SLC_Data['sentences'][i])
    # off.append(SLC_Data['Offset'][i])
    # if(len(SLC_Data['Offset'][i])==0):
    if(SLC_Data['Offset'][i] == '[]'):
        bin_lab_prop.append("no_prop")
    else:
        bin_lab_prop.append("prop")   

In [0]:
set(bin_lab_prop)

{'no_prop', 'prop'}

In [0]:
SLC_Data['label'] = bin_lab_prop

In [0]:
SLC_Data.head()

Unnamed: 0  ...    label
0           0  ...     prop
1           1  ...  no_prop
2           2  ...  no_prop
3           3  ...  no_prop
4           4  ...  no_prop

[5 rows x 4 columns]

In [0]:
SLC_Data['label'].value_counts()

no_prop    12115
prop       12013
Name: label, dtype: int64

In [0]:
import numpy as np
# df1 = df.replace(np.nan, '', regex=True)

SLC_Data['sentences'] = SLC_Data['sentences'].replace(np.nan, '', regex=True)

In [0]:
from sklearn.model_selection import train_test_split
# train, test = train_test_split(SLC_Data, test_size = 0.2)
# train, test = train_test_split(SLC_Data, test_size = 0.0001)

In [0]:
# Creating a config object to store task specific information
class Config(dict):
    def __init__(self, **kwargs):
        super().__init__(**kwargs)
        for k, v in kwargs.items():
            setattr(self, k, v)
    
    def set(self, key, val):
        self[key] = val
        setattr(self, key, val)
        
config = Config(
    testing=False,
    seed = 2019,
    roberta_model_name='roberta-base', # can also be exchnaged with roberta-large 
    # roberta_model_name='roberta-large', # can also be exchnaged with roberta-large 
    max_lr=1e-5,
    epochs=3,
    use_fp16=False,
    # bs=4, 
    # bs=64,
    bs=32,
    # bs=128, 
    max_seq_len=128, 
    num_labels = 2,
    hidden_dropout_prob=.05,
    hidden_size=768, # 1024 for roberta-large
    # hidden_size=1024, # 1024 for roberta-large
    start_tok = "<s>",
    end_tok = "</s>",
)

In [0]:
# df = pd.read_csv("imdb_dataset.csv")
train = SLC_Data
df = SLC_Data
# df = train

In [0]:
# if config.testing: df = df[:5000]
# print(df.shape)

In [0]:
df.head()

Unnamed: 0  ...    label
0           0  ...     prop
1           1  ...  no_prop
2           2  ...  no_prop
3           3  ...  no_prop
4           4  ...  no_prop

[5 rows x 4 columns]

In [0]:
feat_cols = "sentences"
label_cols = "label"

In [0]:
from google.colab import files
files.upload()

Saving Test_Articles_All.csv to Test_Articles_All.csv


{'Test_Articles_All.csv': b',sentences,article_id,startC\n0,"Theresa May Doesn\xe2\x80\x99t Have the Votes\n\nTheresa May still does not appear to have the votes for her deal.",829267754,0\n1,What then?,829267754,102\n2,Extend and PretendEurointelligence says You Really Should Not Take EU\xe2\x80\x99s Willingness to Extend for Granted.,829267754,113\n3,One of the dangers of the Brexit debate is that everybody is making hidden assumptions about what others will do.,829267754,220\n4,One of these assumptions is that the EU would only be too happy to extend the Brexit deadline.,829267754,334\n5,"The EU would, of course, extend to give time for ratification of a deal or even to make way for a cross-party deal.",829267754,429\n6,But Theresa May would have to make clear pretty quickly that this is what she wants to do after the meaningful vote goes against her for a second time \xe2\x80\x93 which may well happen.,829267754,545\n7,"However, the idea that the EU is willing to accept a long exte

In [0]:
import pandas as pd
# Dev_Data = pd.read_csv("dev_articles.csv")
# TestData_Sentences_Article_Id
# Dev_Data = pd.read_csv("TestData_Sentences_Article_Id.csv")
# Dev_Data = pd.read_csv("Dev_Articles_All (1).csv")
Test_Data = pd.read_csv("Test_Articles_All.csv")
Test_Data.head()

Unnamed: 0  ... startC
0           0  ...      0
1           1  ...    102
2           2  ...    113
3           3  ...    220
4           4  ...    334

[5 rows x 4 columns]

In [0]:
print(Dev_Data['startC'][:200])

0         0
1       285
2       468
3       641
4       770
       ... 
195     271
196     560
197     928
198    1058
199    1294
Name: startC, Length: 200, dtype: int64


In [0]:
# test = Dev_Data
test =Test_Data
# dev = Dev_Data

In [0]:
import numpy as np
# df1 = df.replace(np.nan, '', regex=True)

test['sentences'] = test['sentences'].replace(np.nan, '', regex=True)
# dev['sentences'] = dev['sentences'].replace(np.nan, '', regex=True)

## Setting Up the Tokenizer

In [0]:
class FastAiRobertaTokenizer(BaseTokenizer):
    """Wrapper around RobertaTokenizer to be compatible with fastai"""
    def __init__(self, tokenizer: RobertaTokenizer, max_seq_len: int=128, **kwargs): 
        self._pretrained_tokenizer = tokenizer
        self.max_seq_len = max_seq_len 
    def __call__(self, *args, **kwargs): 
        return self 
    def tokenizer(self, t:str) -> List[str]: 
        """Adds Roberta bos and eos tokens and limits the maximum sequence length""" 
        return [config.start_tok] + self._pretrained_tokenizer.tokenize(t)[:self.max_seq_len - 2] + [config.end_tok]

In [0]:
# create fastai tokenizer for roberta
roberta_tok = RobertaTokenizer.from_pretrained("roberta-base")
# roberta_tok = RobertaTokenizer.from_pretrained("roberta-large")

fastai_tokenizer = Tokenizer(tok_func=FastAiRobertaTokenizer(roberta_tok, max_seq_len=config.max_seq_len), 
                             pre_rules=[], post_rules=[])

In [0]:
# create fastai vocabulary for roberta
path = Path()
roberta_tok.save_vocabulary(path)

with open('vocab.json', 'r') as f:
    roberta_vocab_dict = json.load(f)
    
fastai_roberta_vocab = Vocab(list(roberta_vocab_dict.keys()))

In [0]:
# Setting up pre-processors
class RobertaTokenizeProcessor(TokenizeProcessor):
    def __init__(self, tokenizer):
         super().__init__(tokenizer=tokenizer, include_bos=False, include_eos=False)

class RobertaNumericalizeProcessor(NumericalizeProcessor):
    def __init__(self, *args, **kwargs):
        super().__init__(*args, vocab=fastai_roberta_vocab, **kwargs)


def get_roberta_processor(tokenizer:Tokenizer=None, vocab:Vocab=None):
    """
    Constructing preprocessors for Roberta
    We remove sos and eos tokens since we add that ourselves in the tokenizer.
    We also use a custom vocabulary to match the numericalization with the original Roberta model.
    """
    return [RobertaTokenizeProcessor(tokenizer=tokenizer), NumericalizeProcessor(vocab=vocab)]

## Setting up the DataBunch

In [0]:
# Creating a Roberta specific DataBunch class
class RobertaDataBunch(TextDataBunch):
    "Create a `TextDataBunch` suitable for training Roberta"
    @classmethod
    def create(cls, train_ds, valid_ds, test_ds=None, path:PathOrStr='.', bs:int=64, val_bs:int=None, pad_idx=1,
               pad_first=True, device:torch.device=None, no_check:bool=False, backwards:bool=False, 
               dl_tfms:Optional[Collection[Callable]]=None, **dl_kwargs) -> DataBunch:
        "Function that transform the `datasets` in a `DataBunch` for classification. Passes `**dl_kwargs` on to `DataLoader()`"
        datasets = cls._init_ds(train_ds, valid_ds, test_ds)
        val_bs = ifnone(val_bs, bs)
        collate_fn = partial(pad_collate, pad_idx=pad_idx, pad_first=pad_first, backwards=backwards)
        train_sampler = SortishSampler(datasets[0].x, key=lambda t: len(datasets[0][t][0].data), bs=bs)
        train_dl = DataLoader(datasets[0], batch_size=bs, sampler=train_sampler, drop_last=True, **dl_kwargs)
        dataloaders = [train_dl]
        for ds in datasets[1:]:
            lengths = [len(t) for t in ds.x.items]
            sampler = SortSampler(ds.x, key=lengths.__getitem__)
            dataloaders.append(DataLoader(ds, batch_size=val_bs, sampler=sampler, **dl_kwargs))
        return cls(*dataloaders, path=path, device=device, dl_tfms=dl_tfms, collate_fn=collate_fn, no_check=no_check)

In [0]:
class RobertaTextList(TextList):
    _bunch = RobertaDataBunch
    _label_cls = TextList

In [0]:
# loading the tokenizer and vocab processors
processor = get_roberta_processor(tokenizer=fastai_tokenizer, vocab=fastai_roberta_vocab)

# creating our databunch 
data = RobertaTextList.from_df(df, ".", cols=feat_cols, processor=processor) \
    .split_by_rand_pct(seed=config.seed) \
    .label_from_df(cols=label_cols,label_cls=CategoryList) \
    .add_test(RobertaTextList.from_df(test, ".", cols=feat_cols, processor=processor)) \
    .databunch(bs=config.bs, pad_first=False, pad_idx=0)

In [0]:
# # loading the tokenizer and vocab processors
# processor = get_roberta_processor(tokenizer=fastai_tokenizer, vocab=fastai_roberta_vocab)

# # creating our databunch 
# data = RobertaTextList.from_df(df, ".", cols=feat_cols, processor=processor) \
#     .split_by_rand_pct(seed=config.seed) \
#     .label_from_df(cols=label_cols,label_cls=CategoryList) \
#     .databunch(bs=config.bs, pad_first=False, pad_idx=0)

# Building the Model

In [0]:
import torch
import torch.nn as nn
from pytorch_transformers import RobertaModel

# defining our model architecture 
class CustomRobertaModel(nn.Module):
    def __init__(self,num_labels=2):
        super(CustomRobertaModel,self).__init__()
        self.num_labels = num_labels
        self.roberta = RobertaModel.from_pretrained(config.roberta_model_name)
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        self.classifier = nn.Linear(config.hidden_size, num_labels) # defining final output layer
        
    def forward(self, input_ids, token_type_ids=None, attention_mask=None, labels=None):
        _ , pooled_output = self.roberta(input_ids, token_type_ids, attention_mask) # 
        logits = self.classifier(pooled_output)        
        return logits

In [0]:
roberta_model = CustomRobertaModel(num_labels=config.num_labels)
# fbeta
learn = Learner(data, roberta_model, metrics=[accuracy])
# learn = Learner(data, roberta_model, metrics=[accuracy,fbeta])

In [0]:
learn.model.roberta.train() # setting roberta to train as it is in eval mode by default
learn.fit_one_cycle(config.epochs, max_lr=config.max_lr)

# Getting Predictions

In [0]:
def get_preds_as_nparray(ds_type) -> np.ndarray:
    learn.model.roberta.eval()
    preds = learn.get_preds(ds_type)[0].detach().cpu().numpy()
    sampler = [i for i in data.dl(ds_type).sampler]
    reverse_sampler = np.argsort(sampler)
    ordered_preds = preds[reverse_sampler, :]
    pred_values = np.argmax(ordered_preds, axis=1)
    return ordered_preds, pred_values

In [0]:
preds, pred_values = get_preds_as_nparray(list(test["sentences"]))
# preds_dev, pred_values_dev = get_preds_as_nparray(list(dev["sentences"]))

In [0]:
test_preds, test_pred_values = get_preds_as_nparray(DatasetType.Test)
# test_preds_dev, test_pred_value_dev = get_preds_as_nparray(DatasetType.Test)

In [0]:
len(pred_values)

19303

In [0]:
# len(pred_values_dev)

In [0]:
len(test)

In [0]:
len(test_pred_values)

2847

In [0]:
# len(dev), len(test_preds)

In [0]:
test["Bin_Lab"] = test_pred_values

In [0]:
test.head()

In [0]:
test.to_csv('test_binary_prediction_RoBERTa_with_startc_oversample_epoch_2.csv')

In [0]:
df_prop_pred = test[test.Bin_Lab == 1]

In [0]:
df_prop_pred.head()

Unnamed: 0  ... Bin_Lab
11          11  ...       1
12          12  ...       1
27          27  ...       1
42          42  ...       1
49          49  ...       1

[5 rows x 5 columns]

In [0]:
len(df_prop_pred)

771

In [0]:
df_prop_pred.to_csv('test_prop_pred_RoBERTa_startc_oversample_epoch_2.csv')

In [0]:
from google.colab import files
files.download('/content/dev_binary_prediction_RoBERTa_with_startc_paraphrase_oversample_2_epoch_2.csv') 

MessageError: ignored

In [0]:
from google.colab import files
files.download('/content/dev_prop_pred_startc_paraphrase_oversample_2_epoch_2.csv')

In [0]:
test["Bin_Lab"].value_counts()

0    2381
1     428
Name: Bin_Lab, dtype: int64

In [0]:
from sklearn.metrics import classification_report

In [0]:
def label_race (row):
   if row['Label'] == 'propaganda' :
      return 1
   return 0


test["Bin_Label"] = SLC_Data.apply (lambda row: label_race(row), axis=1)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  import sys


In [0]:
len(test["Bin_Label"])

2970

In [0]:
len(test_pred_values)

2970

In [0]:
print(classification_report(test["Bin_Label"], test_pred_values))

              precision    recall  f1-score   support

           0       0.89      0.92      0.91      2318
           1       0.68      0.60      0.64       652

    accuracy                           0.85      2970
   macro avg       0.79      0.76      0.77      2970
weighted avg       0.84      0.85      0.85      2970

